In [54]:
brain_areas = {
    "Frontal lobe" : { "start" : 1, "end" : 68,
                       "sub_areas" : {
                           "Superior frontal gyrus" : { "start" : 1, "end" : 12},
                           "Middle frontal gyrus" : { "start" : 13, "end" : 28},
                           "Inferior frontal gyrus" : { "start" : 29, "end" : 40},
                           "Orbital gyrus" : { "start" : 41, "end" : 52},
                           "Precentral gyrus" : { "start" : 53, "end" : 68}
                       } },
    "Temporal lobe" : { "start" : 69, "end" : 124,
                       "sub_areas" : {
                           "Superior temporal gyrus" : { "start" : 69, "end" : 80},
                           "Middle temporal gyrus" : { "start" : 81, "end" : 88},
                           "Inferior temporal gyrus" : { "start" : 89, "end" : 102},
                           "Fusiform gyrus" : { "start" : 103, "end" : 108},
                           "Parahippocampal gyrus" : { "start" : 109, "end" : 120},
                           "Posterior superior temporal sulcus" : { "start" : 121, "end" : 124}
                       } },
    "Parietal lobe" : { "start" : 125, "end" : 162,
                       "sub_areas" : {
                           "Superior parietal lobule" : { "start" : 125, "end" : 134},
                           "Inferior parietal lobule" : { "start" : 135, "end" : 146},
                           "Precuneus" : { "start" : 147, "end" : 154},
                           "Postcentral gyrus" : { "start" : 155, "end" : 162}
                       } },
    "Insular lobule" : { "start" : 163, "end" : 174,
                        "sub_areas" : {
                            "Insular gyrus" : { "start" : 163, "end" : 174},
                        } },
    "Limbic lobe" : { "start" : 175, "end" : 188,
                      "sub_areas" : {
                          "Cingulate gyrus" : { "start" : 175, "end" : 188},
                      } },
    "Occipital lobe" : { "start" : 189, "end" : 210,
                         "sub_areas" : {
                             "MedioVentral occipital cortex" : { "start" : 189, "end" : 198},
                             "Cuneus" : { "start" : 199, "end" : 210},
                         } },
    "Subcortical nuclei" : { "start" : 211, "end" : 246,
                             "sub_areas" : {
                                 "Amygdala" : { "start" : 211, "end" : 214},
                                 "Hippocampus" : { "start" : 215, "end" : 218},
                                 "Basal ganglia" : { "start" : 219, "end" : 230},
                                 "Thalamus" : { "start" : 231, "end" : 246},
                             } },   
    "Cerebellum" : { "start" : 247, "end" : 274}
}

In [55]:
import nibabel as nib
import numpy as np


md_path = 'Sub2_MD.nii'
atlas_path = 'Sub2_AtlasBNA.nii'
md_img = nib.load(md_path)
atlas_img = nib.load(atlas_path)

md_data = md_img.get_fdata()
atlas_data = atlas_img.get_fdata()
md_data = np.where(md_data > 0.00225, 0.00225, md_data)

regions_mask = atlas_data >= 1


value_mask = md_data < 0.0004


combined_mask = np.logical_and(regions_mask, value_mask)


md_data[combined_mask] = 0.0004

In [56]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

def plot_md_values_for_regions_jupyter(start_region, end_region, marker_size=5):
  
    regions_of_interest = list(range(start_region, end_region + 1))

    
    filtered_data_list = []

    
    for x in range(atlas_data.shape[0]):
        for y in range(atlas_data.shape[1]):
            for z in range(atlas_data.shape[2]):
                region = int(atlas_data[x, y, z])
                if region in regions_of_interest:
                    md_value = md_data[x, y, z]
                    filtered_data_list.append([x, y, z, region, md_value])

    
    filtered_df = pd.DataFrame(filtered_data_list, columns=['X', 'Y', 'Z', 'Region', 'MD_Value'])

    
    hover_text = [
        f"X: {x}<br>Y: {y}<br>Z: {z}<br>MD Value: {md_value:.4f}<br>Region: {region}" 
        for x, y, z, region, md_value in zip(filtered_df['X'], filtered_df['Y'], filtered_df['Z'], filtered_df['Region'], filtered_df['MD_Value'])
    ]

    
    min_md_value = filtered_df['MD_Value'].min()
    max_md_value = filtered_df['MD_Value'].max()
    colorbar_title = f'MD Value<br>Min: {min_md_value:.4f}<br>Max: {max_md_value:.4f}'

    fig = go.Figure(data=[go.Scatter3d(
        x=filtered_df['X'],
        y=filtered_df['Y'],
        z=filtered_df['Z'],
        mode='markers',
        marker=dict(
            size=marker_size,  
            color=filtered_df['MD_Value'], 
            colorscale='hsv',  
            colorbar=dict(title=colorbar_title),
            opacity=0.8  
        ),
        text=hover_text, 
        hoverinfo='text'
    )])


    fig.update_layout(
        title=f'3D Scatter Plot of MD Values for Regions {start_region}-{end_region}',
        paper_bgcolor='white',
        plot_bgcolor='white',
        scene=dict(
            xaxis=dict(backgroundcolor="white", gridcolor="lightgrey", showbackground=True, zerolinecolor="white"),
            yaxis=dict(backgroundcolor="white", gridcolor="lightgrey", showbackground=True, zerolinecolor="white"),
            zaxis=dict(backgroundcolor="white", gridcolor="lightgrey", showbackground=True, zerolinecolor="white"),
            xaxis_title='X Axis',
            yaxis_title='Y Axis',
            zaxis_title='Z Axis'
        )
    )


    fig.update_traces(marker=dict(line=dict(width=0)), selector=dict(type='scatter3d'))

    fig.show()


In [58]:
plot_md_values_for_regions_jupyter(211, 246)